# Assignment 5 - Text Analysis
An explanation this assignment could be found in the .pdf explanation document


## Materials to review for this assignment
<h4>From Moodle:</h4> 
<h5><u>Review the notebooks regarding the following python topics</u>:</h5>
<div class="alert alert-info">
&#x2714; <b>Working with strings</b> (tutorial notebook)<br/>
&#x2714; <b>Text Analysis</b> (tutorial notebook)<br/>
&#x2714; <b>Hebrew text analysis tools (tokenizer, wordnet)</b> (moodle example)<br/>
&#x2714; <b>(brief review) All previous notebooks</b><br/>
</div> 
<h5><u>Review the presentations regarding the following topics</u>:</h5>
<div class="alert alert-info">
&#x2714; <b>Text Analysis</b> (lecture presentation)<br/>
&#x2714; <b>(brief review) All other presentations</b><br/>
</div>

## Preceding Step - import modules (packages)
This step is necessary in order to use external modules (packages). <br/>

In [1]:
# --------------------------------------
import pandas as pd
import numpy as np
# --------------------------------------


# --------------------------------------
# ------------- visualizations:
import seaborn as sns
import matplotlib.pyplot as plt
from matplotlib.colors import ListedColormap
# --------------------------------------


# ---------------------------------------
import sklearn
from sklearn import preprocessing, metrics, pipeline, model_selection, feature_extraction 
from sklearn import naive_bayes, linear_model, svm, neural_network, neighbors, tree
from sklearn import decomposition, cluster

from sklearn.model_selection import train_test_split, cross_val_score, GridSearchCV 
from sklearn.pipeline import Pipeline
from sklearn.metrics import accuracy_score, confusion_matrix
from sklearn.metrics import precision_score, recall_score, f1_score
from sklearn.metrics import mean_squared_error, r2_score, silhouette_score
from sklearn.preprocessing import MinMaxScaler, StandardScaler, LabelEncoder

from sklearn.svm import LinearSVC
from sklearn.neural_network import MLPClassifier
from sklearn.linear_model import Perceptron, SGDClassifier
from sklearn.decomposition import PCA
from sklearn.cluster import KMeans
from sklearn.naive_bayes import MultinomialNB, GaussianNB
from sklearn.neighbors import KNeighborsClassifier
from sklearn.tree import DecisionTreeClassifier
# ---------------------------------------


# ----------------- output and visualizations: 
import warnings
from sklearn.exceptions import ConvergenceWarning
warnings.simplefilter("ignore")
warnings.simplefilter(action='ignore', category=FutureWarning)
warnings.simplefilter("ignore", category=ConvergenceWarning)
# show several prints in one cell. This will allow us to condence every trick in one cell.
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"
%matplotlib inline
pd.pandas.set_option('display.max_columns', None)
pd.set_option('display.float_format', lambda x: '%.3f' % x)
# ---------------------------------------

### Text analysis and String manipulation imports:

In [2]:
# --------------------------------------
# --------- Text analysis and Hebrew text analysis imports:
# vectorizers:
from sklearn.feature_extraction import text
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer

# regular expressions:
import re
# --------------------------------------

### (optional) Hebrew text analysis - WordNet (for Hebrew)
Note: the WordNet is not a must

#### (optional) Only if you didn't install Wordnet (for Hebrew) use:

In [3]:
# word net installation:

# unmark if you want to use and need to install
# !pip install wn
# !python -m wn download omw-he:1.4

In [4]:
# word net import:

# unmark if you want to use:
# import wn

### (optional) Hebrew text analysis - hebrew_tokenizer (Tokenizer for Hebrew)
Note: the hebrew_tokenizer is not a must

#### (optional) Only if you didn't install hebrew_tokenizer use:

In [5]:
# Hebrew tokenizer installation:

# unmark if you want to use and need to install:
!pip install hebrew_tokenizer

In [6]:
# Hebrew tokenizer import:

# unmark if you want to use:
import hebrew_tokenizer as ht

C:\Users\eliy5\OneDrive\Desktop\ml-text-analysis


### Reading input files
Reading input files for train annotated corpus (raw text data) corpus and for the test corpus

In [7]:
train_filename = 'annotated_corpus_for_train.csv'
test_filename  = 'corpus_for_test.csv'
df_train = pd.read_csv(train_filename, index_col=None, encoding='utf-8')
df_test  = pd.read_csv(test_filename, index_col=None, encoding='utf-8')

In [8]:
df_train.head(8)
df_train.shape

story gender
0  כשחבר הזמין אותי לחול, לא באמת חשבתי שזה יקרה,...      m
1  לפני שהתגייסתי לצבא עשיתי כל מני מיונים ליחידו...      m
2  מאז שהתחילו הלימודים חלומו של כל סטודנט זה הפנ...      f
3  כשהייתי ילד, מטוסים היה הדבר שהכי ריתק אותי. ב...      m
4  ‏הייתי מדריכה בכפר נוער ומתאם הכפר היינו צריכי...      f
5  לפני כ3 חודשים טסתי לרומא למשך שבוע. טסתי במטו...      f
6  אני כבר שנתיים נשוי והשנה אני ואישתי סוף סוף י...      m
7  השנה התחלנו שיפוץ בדירה שלנו בתל אביב. הדירה ה...      f

(753, 2)

In [9]:
df_test.head(3)
df_test.shape

test_example_id                                              story
0                0  כל קיץ אני והמשפחה נוסעים לארצות הברית לוס אנג...
1                1  הגעתי לשירות המדינה אחרי שנתיים כפעיל בתנועת "...
2                2  אחת האהבות הגדולות שלי אלו הכלבים שלי ושל אישת...

(323, 2)

### Your implementation:
Write your code solution in the following code-cells

In [60]:
#PREPARE DATA AND CLEAN

#remove signs and leave only hebrew words
#change gender to numbers

def clean_story(df):
    chars_to_remove = ['.' , ',' , '?' , '!' , ':', ';' , '(' , ')', '"' , "'"]

    for c in chars_to_remove:
        df['story'] = df['story'].str.replace(c, '')

    df['story'] = df['story'].apply(lambda x: re.sub(r'[^\u0590-\u05FF ]', '', x))

    return df

def set_male_female(df):
    
    df['gender'] = df['gender'].str.replace("m", '0')
    df['gender'] = df['gender'].str.replace("f", '1')

    return df

#CLEAN TRAIN
df_train = clean_story(df_train)

#CLEAN TEST
df_test = clean_story(df_test)

#GENDERS
df_train = set_male_female(df_train)
df_train



story gender
0    כשחבר הזמין אותי לחול לא באמת חשבתי שזה יקרה פ...      0
1    לפני שהתגייסתי לצבא עשיתי כל מני מיונים ליחידו...      0
2    מאז שהתחילו הלימודים חלומו של כל סטודנט זה הפנ...      1
3    כשהייתי ילד מטוסים היה הדבר שהכי ריתק אותי בתו...      0
4    הייתי מדריכה בכפר נוער ומתאם הכפר היינו צריכים...      1
..                                                 ...    ...
748  אז לפני שנה בדיוק טסתי לאמסטרדם עם שני חברים ט...      0
749  שבוע שעבר העליתי באופן ספונטני רעיון לנסוע עם ...      0
750  לפני חודש עברנו לדירה בבית שמש בעקבות משפחתי ה...      0
751  החוויה אותה ארצה לשתף התרחשה לפני כמה חודשים ז...      1
752  פעם כשהייתי בחו ל בקבולומביה כחלק מהטיול שלי ל...      0

[753 rows x 2 columns]

In [11]:
#VECTORIZE train and test
#count 1 or 2 words together

cv = CountVectorizer(ngram_range=(1,2) , min_df=5)
X = cv.fit(df_train['story'])
X = cv.transform(df_train['story'])

df_train_vectorized = pd.DataFrame(X.toarray(), columns = cv.get_feature_names())

Y = cv.transform(df_test['story'])
df_test_vectorized = pd.DataFrame(Y.toarray(), columns = cv.get_feature_names())
df_test_vectorized.shape

(323, 9615)

In [12]:
df_train_vectorized['gender'] = df_train['gender']


In [13]:
df_train_vectorized.head(10)


אבא  אבא שלו  אבא שלי  אבי  אביב  אביב כדי  אבל  אבל אז  אבל אחרי  אבל אין  \
0    0        0        0    0     0         0    4       0         0        0   
1    0        0        0    0     0         0    1       0         0        0   
2    0        0        0    0     0         0    5       0         2        0   
3    5        0        5    0     0         0    2       0         0        0   
4    0        0        0    0     0         0    2       0         0        0   
5    0        0        0    0     0         0    0       0         0        0   
6    0        0        0    0     0         0    3       0         0        0   
7    0        0        0    0     1         0    0       0         0        0   
8    0        0        0    0     1         0    2       0         0        0   
9    0        0        0    0     0         0    2       0         0        0   

   אבל אמרתי  אבל אני  אבל בגלל  אבל בכל  אבל בסופו  אבל גם  אבל האמת  \
0          0        0         0        0          0       0         0   
1          0        1         0        0          0       0         0   
2          0        1         0        0          0       0         0   
3          0        0         0        0          0       0         0   
4          0        0         0        0          0       0         0   
5          0        0         0        0          0       0         0   
6          0        0         0        0          0       0         0   
7          0        0         0        0          0       0         0   
8          2        0         0        0          0       0         0   
9          0        0         0        0          0       0         0   

   אבל הוא  אבל החלטנו  אבל היא  אבל היה  אבל היו  אבל הייתי  אבל הכי  אבל הם  \
0        0           0        0        0        0          0        0       0   
1        0           0        0        0        0          0        0       0   
2        0           0        0        0        0          0        0       0   
3        0           0        0        0        0          0        0       0   
4        0           0        0        0        0          0        0       0   
5        0           0        0        0        0          0        0       0   
6        0           0        0        0        0          0        0       0   
7        0           0        0        0        0          0        0       0   
8        0           0        0        0        0          0        0       0   
9        0           0        0        0        0          0        0       1   

   אבל הפעם  אבל זה  אבל יש  אבל כבר  אבל כל  אבל כמובן  אבל כן  אבל לא  \
0         0       0       0        0       1          0       0       0   
1         0       0       0        0       0          0       0       0   
2         0       0       0        0       0          0       0       0   
3         1       0       0        0       0          0       0       0   
4         0       0       0        0       0          0       0       0   
5         0       0       0        0       0          0       0       0   
6         0       0       0        0       0          0       0       0   
7         0       0       0        0       0          0       0       0   
8         0       0       0        0       0          0       0       0   
9         0       0       0        0       0          0       0       0   

   אבל לאחר  אבל לי  אבל ללא  אבל למרות  אבל לפחות  אבל מה  אבל מצד  \
0         1       0        0          0          0       0        0   
1         0       0        0          0          0       0        0   
2         0       0        0          0          1       1        0   
3         0       0        0          0          0       0        0   
4         0       0        0          0          0       0        0   
5         0       0        0          0          0       0        0   
6         0       0        0          0          0       0        0   
7         0       0  

In [14]:
#split train data

def split_my_data(data):
    training_data, testing_data = train_test_split(data, test_size=0.2, random_state=25)
    y_train = training_data['gender']
    y_test = testing_data['gender']
    del training_data['gender']
    del testing_data['gender']

    return training_data , y_train , testing_data , y_test

training_data , y_train , testing_data , y_test = split_my_data(df_train_vectorized)


In [15]:
#get best knn model 

def get_best_knn(X_train, X_test, y_train, y_test):
    best_clf = None
    best_acc = 0

    # Define the parameter grid
    param_grid = {
        'n_neighbors': [3, 5, 7, 9, 11, 13, 15],
        'weights': ['uniform', 'distance'],
        'metric': ['euclidean', 'manhattan', 'minkowski']
    }

    # Initialize a KNN classifier
    knn = KNeighborsClassifier()

    # Initialize a Grid Search object
    grid_search = GridSearchCV(
        knn, 
        param_grid, 
        cv=5,  # Number of folds in cross-validation
        scoring='accuracy',  
        verbose=1,  # Print messages while running
        n_jobs=-1  # Use all available cores
    )

    # Fit the Grid Search object to the data
    grid_search.fit(X_train, y_train)

    # Get the best classifier
    best_clf = grid_search.best_estimator_

    # Predict the test data
    y_pred = best_clf.predict(X_test)

    best_acc = accuracy_score(y_test, y_pred)
    male_f1 = f1_score(y_test, y_pred , pos_label='0')
    female_f1 = f1_score(y_test, y_pred , pos_label='1')
    avarage_f1 = (male_f1+ female_f1) /2

    
    
    # Return the best classifier and its accuracy
    return {"best_clf" : best_clf, "best_acc": best_acc , "male_f1" : male_f1 , "female_f1" : female_f1 , "avarage_f1" : avarage_f1}

best_knn = get_best_knn(training_data ,  testing_data , y_train  , y_test)


Fitting 5 folds for each of 42 candidates, totalling 210 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 6 concurrent workers.
[Parallel(n_jobs=-1)]: Done  38 tasks      | elapsed:   12.7s
[Parallel(n_jobs=-1)]: Done 188 tasks      | elapsed:   50.7s
[Parallel(n_jobs=-1)]: Done 210 out of 210 | elapsed:   56.1s finished


In [16]:
#test models of DecisionTreeClassifier


def get_best_dt(X_train, X_test, y_train, y_test):
    # Define the parameter grid
    param_grid = {
        'criterion': ['gini', 'entropy'],
        'max_depth': [1, 2, 3, 4, 5, 6, 7, 8, 9, 10]
    }

    # Initialize a Decision Tree classifier
    dt = DecisionTreeClassifier()

    # Initialize a Grid Search object
    grid_search = GridSearchCV(
        dt, 
        param_grid, 
        cv=5,  # Number of folds in cross-validation
        scoring="accuracy",
        verbose=1,  # Print messages while running
        n_jobs=-1  # Use all available cores
    )

    # Fit the Grid Search object to the data
    grid_search.fit(X_train, y_train)

    # Get the best classifier
    best_clf = grid_search.best_estimator_

    # Predict the test data
    y_pred = best_clf.predict(X_test)

    best_acc = accuracy_score(y_test, y_pred)
    male_f1 = f1_score(y_test, y_pred , pos_label='0')
    female_f1 = f1_score(y_test, y_pred , pos_label='1')
    avarage_f1 = (male_f1+ female_f1) /2

    
    
    # Return the best classifier and its accuracy
    return {"best_clf" : best_clf, "best_acc": best_acc , "male_f1" : male_f1 , "female_f1" : female_f1 , "avarage_f1" : avarage_f1}



In [17]:
best_dt = get_best_dt(training_data ,  testing_data , y_train  , y_test)
best_dt

Fitting 5 folds for each of 20 candidates, totalling 100 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 6 concurrent workers.
[Parallel(n_jobs=-1)]: Done  64 tasks      | elapsed:    5.3s
[Parallel(n_jobs=-1)]: Done 100 out of 100 | elapsed:    8.9s finished


{'best_clf': DecisionTreeClassifier(ccp_alpha=0.0, class_weight=None, criterion='entropy',
                        max_depth=3, max_features=None, max_leaf_nodes=None,
                        min_impurity_decrease=0.0, min_impurity_split=None,
                        min_samples_leaf=1, min_samples_split=2,
                        min_weight_fraction_leaf=0.0, presort='deprecated',
                        random_state=None, splitter='best'),
 'best_acc': 0.7086092715231788,
 'male_f1': 0.8253968253968255,
 'female_f1': 0.12000000000000001,
 'avarage_f1': 0.47269841269841273}

In [19]:
from sklearn.linear_model import LogisticRegression

def get_best_lg(X_train, X_test, y_train, y_test):
    # Define the parameter grid
    param_grid = {
        'penalty': ['l1', 'l2'],
        'C': [0.01, 0.1, 1, 10, 100, 1000],
        'solver': ['newton-cg', 'lbfgs', 'liblinear', 'sag']
    }

    # Initialize a Logistic Regression classifier
    logreg = LogisticRegression()

    # Initialize a Grid Search object
    grid_search = GridSearchCV(
        logreg, 
        param_grid, 
        cv=5,  # Number of folds in cross-validation
        scoring="accuracy",  # Use F1 score as the scoring metric
        verbose=1,  # Print messages while running
        n_jobs=-1  # Use all available cores
    )

    # Fit the Grid Search object to the data
    grid_search.fit(X_train, y_train)

    # Get the best classifier
    best_clf = grid_search.best_estimator_

    # Predict the test data
    y_pred = best_clf.predict(X_test)

    best_acc = accuracy_score(y_test, y_pred)
    male_f1 = f1_score(y_test, y_pred , pos_label='0')
    female_f1 = f1_score(y_test, y_pred , pos_label='1')
    avarage_f1 = (male_f1+ female_f1) /2

    
    
    # Return the best classifier and its accuracy
    return {"best_clf" : best_clf, "best_acc": best_acc , "male_f1" : male_f1 , "female_f1" : female_f1 , "avarage_f1" : avarage_f1}


best_logreg = get_best_lg(training_data ,  testing_data , y_train  , y_test)


Fitting 5 folds for each of 48 candidates, totalling 240 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 6 concurrent workers.
[Parallel(n_jobs=-1)]: Done  89 tasks      | elapsed:    9.4s
[Parallel(n_jobs=-1)]: Done 240 out of 240 | elapsed:   36.4s finished


In [20]:
best_logreg

{'best_clf': LogisticRegression(C=1000, class_weight=None, dual=False, fit_intercept=True,
                    intercept_scaling=1, l1_ratio=None, max_iter=100,
                    multi_class='auto', n_jobs=None, penalty='l1',
                    random_state=None, solver='liblinear', tol=0.0001, verbose=0,
                    warm_start=False),
 'best_acc': 0.7483443708609272,
 'male_f1': 0.8389830508474577,
 'female_f1': 0.4242424242424242,
 'avarage_f1': 0.631612737544941}

In [21]:
from sklearn.svm import SVC

def get_best_svc(X_train, X_test, y_train, y_test):

    param_grid = {
        'C': [0.01, 0.1, 1, 10, 100], 'kernel': ['linear', 'rbf']
    }

    # Initialize an SVC classifier
    svc = SVC()

    # Initialize a Grid Search object
    grid_search = GridSearchCV(
        svc, 
        param_grid, 
        cv=5,  # Number of folds in cross-validation
        scoring="accuracy",  # Use F1 score as the scoring metric
        verbose=1,  # Print messages while running
        n_jobs=-1  # Use all available cores
    )

    # Fit the Grid Search object to the data
    grid_search.fit(X_train, y_train)

    # Get the best classifier
    best_clf = grid_search.best_estimator_

    # Predict the test data
    y_pred = best_clf.predict(X_test)

    best_acc = accuracy_score(y_test, y_pred)
    male_f1 = f1_score(y_test, y_pred , pos_label='0')
    female_f1 = f1_score(y_test, y_pred , pos_label='1')
    avarage_f1 = (male_f1+ female_f1) /2

    
    
    # Return the best classifier and its accuracy
    return {"best_clf" : best_clf, "best_acc": best_acc , "male_f1" : male_f1 , "female_f1" : female_f1 , "avarage_f1" : avarage_f1}



In [22]:
best_svc= get_best_svc(training_data ,  testing_data , y_train  , y_test)
best_svc

Fitting 5 folds for each of 10 candidates, totalling 50 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 6 concurrent workers.
[Parallel(n_jobs=-1)]: Done  38 tasks      | elapsed:   26.8s
[Parallel(n_jobs=-1)]: Done  50 out of  50 | elapsed:   33.5s finished


{'best_clf': SVC(C=0.1, break_ties=False, cache_size=200, class_weight=None, coef0=0.0,
     decision_function_shape='ovr', degree=3, gamma='scale', kernel='linear',
     max_iter=-1, probability=False, random_state=None, shrinking=True,
     tol=0.001, verbose=False),
 'best_acc': 0.7284768211920529,
 'male_f1': 0.8225108225108225,
 'female_f1': 0.4225352112676057,
 'avarage_f1': 0.6225230168892141}

In [23]:

def get_best_LinearSVC(X_train, X_test, y_train, y_test):
    # Define the parameter grid
    param_grid = {
        'C': [0.1, 1, 10, 100, 1000],
        'penalty': ['l1', 'l2'],
        'dual': [False]  # 'dual=False' when n_samples > n_features.
    }

    # Initialize a LinearSVC classifier
    lsvc = LinearSVC()

    # Initialize a Grid Search object
    grid_search = GridSearchCV(
        lsvc, 
        param_grid, 
        cv=5,  # Number of folds in cross-validation
        scoring="accuracy",  # Use F1 score as the scoring metric
        verbose=1,  # Print messages while running
        n_jobs=-1  # Use all available cores
    )

    # Fit the Grid Search object to the data
    grid_search.fit(X_train, y_train)

    # Get the best classifier
    best_clf = grid_search.best_estimator_

    # Predict the test data
    y_pred = best_clf.predict(X_test)

    best_acc = accuracy_score(y_test, y_pred)
    male_f1 = f1_score(y_test, y_pred , pos_label='0')
    female_f1 = f1_score(y_test, y_pred , pos_label='1')
    avarage_f1 = (male_f1+ female_f1) /2

    
    
    # Return the best classifier and its accuracy
    return {"best_clf" : best_clf, "best_acc": best_acc , "male_f1" : male_f1 , "female_f1" : female_f1 , "avarage_f1" : avarage_f1}


In [24]:
best_LinearSVC = get_best_LinearSVC(training_data ,  testing_data , y_train  , y_test)
best_LinearSVC

Fitting 5 folds for each of 10 candidates, totalling 50 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 6 concurrent workers.
[Parallel(n_jobs=-1)]: Done  39 out of  50 | elapsed:    1.9s remaining:    0.5s
[Parallel(n_jobs=-1)]: Done  50 out of  50 | elapsed:    2.4s finished


{'best_clf': LinearSVC(C=10, class_weight=None, dual=False, fit_intercept=True,
           intercept_scaling=1, loss='squared_hinge', max_iter=1000,
           multi_class='ovr', penalty='l2', random_state=None, tol=0.0001,
           verbose=0),
 'best_acc': 0.7086092715231788,
 'male_f1': 0.8103448275862069,
 'female_f1': 0.37142857142857144,
 'avarage_f1': 0.5908866995073891}

In [25]:

def get_best_mlp(X_train, X_test, y_train, y_test):
    # Define the parameter grid
    param_grid = {
        'hidden_layer_sizes': [(50,50,50), (50,100,50), (100,)],
        'activation': ['tanh', 'relu'],
        'solver': ['sgd', 'adam'],
        'alpha': [0.0001, 0.05],
        'learning_rate': ['constant','adaptive'],
    }

    # Initialize an MLP classifier
    mlp = MLPClassifier(max_iter=100)

    # Initialize a Grid Search object
    grid_search = GridSearchCV(
        mlp, 
        param_grid, 
        cv=5,  # Number of folds in cross-validation
        scoring="accuracy",  # Use F1 score as the scoring metric
        verbose=1,  # Print messages while running
        n_jobs=-1  # Use all available cores
    )

    # Fit the Grid Search object to the data
    grid_search.fit(X_train, y_train)

    # Get the best classifier
    best_clf = grid_search.best_estimator_

    # Predict the test data
    y_pred = best_clf.predict(X_test)

    best_acc = accuracy_score(y_test, y_pred)
    male_f1 = f1_score(y_test, y_pred , pos_label='0')
    female_f1 = f1_score(y_test, y_pred , pos_label='1')
    avarage_f1 = (male_f1+ female_f1) /2

    # Return the best classifier and its accuracy
    return {"best_clf" : best_clf, "best_acc": best_acc , "male_f1" : male_f1 , "female_f1" : female_f1 , "avarage_f1" : avarage_f1}

best_mlp = get_best_mlp(training_data ,  testing_data , y_train  , y_test)
best_mlp

Fitting 5 folds for each of 48 candidates, totalling 240 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 6 concurrent workers.
[Parallel(n_jobs=-1)]: Done  38 tasks      | elapsed:  1.7min
[Parallel(n_jobs=-1)]: Done 188 tasks      | elapsed: 11.8min
[Parallel(n_jobs=-1)]: Done 240 out of 240 | elapsed: 15.9min finished


{'best_clf': MLPClassifier(activation='relu', alpha=0.05, batch_size='auto', beta_1=0.9,
               beta_2=0.999, early_stopping=False, epsilon=1e-08,
               hidden_layer_sizes=(50, 100, 50), learning_rate='constant',
               learning_rate_init=0.001, max_fun=15000, max_iter=100,
               momentum=0.9, n_iter_no_change=10, nesterovs_momentum=True,
               power_t=0.5, random_state=None, shuffle=True, solver='adam',
               tol=0.0001, validation_fraction=0.1, verbose=False,
               warm_start=False),
 'best_acc': 0.695364238410596,
 'male_f1': 0.8050847457627118,
 'female_f1': 0.30303030303030304,
 'avarage_f1': 0.5540575243965075}

In [26]:
def get_best_sgd(X_train, X_test, y_train, y_test):
    # Define the parameter grid
    param_grid = {
        'loss': ['hinge', 'log', 'modified_huber', 'squared_hinge', 'perceptron'],
        'penalty': ['l2', 'l1', 'elasticnet'],
        'alpha': [0.0001, 0.05]
    }

    # Initialize an SGD classifier
    sgd = SGDClassifier()

    # Initialize a Grid Search object
    grid_search = GridSearchCV(
        sgd, 
        param_grid, 
        cv=5,  # Number of folds in cross-validation
        scoring="accuracy",  
        verbose=1,  # Print messages while running
        n_jobs=-1  # Use all available cores
    )

    # Fit the Grid Search object to the data
    grid_search.fit(X_train, y_train)

    # Get the best classifier
    best_clf = grid_search.best_estimator_

    # Predict the test data
    y_pred = best_clf.predict(X_test)

    best_acc = accuracy_score(y_test, y_pred)
    male_f1 = f1_score(y_test, y_pred , pos_label='0')
    female_f1 = f1_score(y_test, y_pred , pos_label='1')
    avarage_f1 = (male_f1+ female_f1) /2

    # Return the best classifier and its accuracy
    return {"best_clf" : best_clf, "best_acc": best_acc , "male_f1" : male_f1 , "female_f1" : female_f1 , "avarage_f1" : avarage_f1}

best_sgd = get_best_sgd(training_data ,  testing_data , y_train  , y_test)
best_sgd

Fitting 5 folds for each of 30 candidates, totalling 150 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 6 concurrent workers.
[Parallel(n_jobs=-1)]: Done  38 tasks      | elapsed:    3.0s
[Parallel(n_jobs=-1)]: Done 150 out of 150 | elapsed:   45.6s finished


{'best_clf': SGDClassifier(alpha=0.0001, average=False, class_weight=None,
               early_stopping=False, epsilon=0.1, eta0=0.0, fit_intercept=True,
               l1_ratio=0.15, learning_rate='optimal', loss='perceptron',
               max_iter=1000, n_iter_no_change=5, n_jobs=None,
               penalty='elasticnet', power_t=0.5, random_state=None,
               shuffle=True, tol=0.001, validation_fraction=0.1, verbose=0,
               warm_start=False),
 'best_acc': 0.7284768211920529,
 'male_f1': 0.8326530612244898,
 'female_f1': 0.2807017543859649,
 'avarage_f1': 0.5566774078052273}

In [44]:
#best model
models = [best_knn , best_dt, best_svc , best_LinearSVC , best_mlp , best_logreg , best_sgd]

print('All Models:')
print('\n')
print('\n')
for model in models:
    bestf1 = 0
    best_model = None
    print("Model: " , model['best_clf'])
    print("Accuracy: ",model['best_acc'])
    print("Male f1: ",model['male_f1'])
    print("Female f1: ",model['female_f1'])
    print("Avarage F1: ",model['avarage_f1'])

    print('\n')
    print('\n')

    if(model['avarage_f1'] > bestf1):
        bestf1 = model['avarage_f1']
        best_model = model


All Models:




Model:  KNeighborsClassifier(algorithm='auto', leaf_size=30, metric='euclidean',
                     metric_params=None, n_jobs=None, n_neighbors=9, p=2,
                     weights='uniform')
Accuracy:  0.7019867549668874
Male f1:  0.8235294117647058
Female f1:  0.04255319148936171
Avarage F1:  0.4330413016270338




Model:  DecisionTreeClassifier(ccp_alpha=0.0, class_weight=None, criterion='entropy',
                       max_depth=3, max_features=None, max_leaf_nodes=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, presort='deprecated',
                       random_state=None, splitter='best')
Accuracy:  0.7086092715231788
Male f1:  0.8253968253968255
Female f1:  0.12000000000000001
Avarage F1:  0.47269841269841273




Model:  SVC(C=0.1, break_ties=False, cache_size=200, class_weight=None, coef0=0.0,
    decision_fun

In [47]:
print('The Best Model:')
print('\n')
print('\n')
print("Model: " , best_model['best_clf'])
print("Accuracy: ",best_model['best_acc'])
print("Male f1: ",best_model['male_f1'])
print("Female f1: ",best_model['female_f1'])
print("Avarage F1: ",best_model['avarage_f1'])

The Best Model:




Model:  SGDClassifier(alpha=0.0001, average=False, class_weight=None,
              early_stopping=False, epsilon=0.1, eta0=0.0, fit_intercept=True,
              l1_ratio=0.15, learning_rate='optimal', loss='perceptron',
              max_iter=1000, n_iter_no_change=5, n_jobs=None,
              penalty='elasticnet', power_t=0.5, random_state=None,
              shuffle=True, tol=0.001, validation_fraction=0.1, verbose=0,
              warm_start=False)
Accuracy:  0.7284768211920529
Male f1:  0.8326530612244898
Female f1:  0.2807017543859649
Avarage F1:  0.5566774078052273


In [54]:
#predict final solution
y = best_model['best_clf'].predict(df_test_vectorized)
y

array(['0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '1', '0', '0',
       '0', '1', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0',
       '0', '0', '0', '0', '0', '0', '1', '0', '0', '1', '0', '0', '0',
       '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '1', '0',
       '1', '0', '0', '0', '0', '0', '0', '1', '0', '0', '0', '0', '1',
       '0', '0', '0', '0', '0', '0', '0', '0', '1', '0', '0', '0', '0',
       '0', '0', '0', '0', '0', '0', '0', '0', '0', '1', '0', '0', '0',
       '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0',
       '0', '0', '0', '0', '1', '0', '0', '0', '1', '0', '0', '0', '0',
       '0', '0', '0', '0', '0', '0', '0', '0', '1', '0', '1', '0', '0',
       '0', '0', '0', '0', '1', '1', '0', '0', '0', '0', '0', '1', '0',
       '1', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0',
       '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0',
       '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0', '0

In [55]:
df_test['pred'] = y

In [59]:
df_test.head(40)
print("...")

test_example_id                                              story pred
0                 0  כל קיץ אני והמשפחה נוסעים לארצות הברית לוס אנג...    0
1                 1  הגעתי לשירות המדינה אחרי שנתיים כפעיל בתנועת י...    0
2                 2  אחת האהבות הגדולות שלי אלו הכלבים שלי ושל אישת...    0
3                 3  רגע הגיוס לצבא היה הרגע הכי משמעותי עבורי אני ...    0
4                 4  אני הגעתי לברזיל ישר מקולומביה וגם אני עשיתי ע...    0
5                 5  בפעם האחרונה שהייתי מחוץ לארץ ישראל הייתי באפר...    0
6                 6  בשנת  קיבלתי החלטה שאני מתחיל ללמוד לתואר ראשו...    0
7                 7  בנובמבר האחרון הייתי עם חברים בטיול ים אל ים ה...    0
8                 8  לפני מספר חודשים ביום שמש בהיר קמתי בבוקר למה ...    0
9                 9  אני לא בן אדם שנוטה לשתף בחייו האישיים אבל אול...    0
10               10  לפני כמה זמן בדרך הביתה שמעתי איך כלבים נובחים...    1
11               11  חיכיתי לסוף שנת הלימודים הרבה מאוד זמן  כדי למ...    0
12               12  השנה שנת הקורונה הייתה בשבילי שנה עם הרבה זמן ...    0
13               13  החוויה שלי מתחילה במכון הטכנולוגי חולון אשר שע...    0
14               14  לפני פחות משנה יחסית בתחילת התפשטות הקורונה שע...    1
15               15  לפני כשנה מסרתי את אחד הדברים היקרים שהיו לי ב...    0
16               16  לפני כמעט שנה מעט אחרי התפרצות הקורונה נסענו כ...    0
17               17  בסוף הצבא החלטנו אני ועוד כמה חברים לעשות טיול...    0
18               18  החוויה הראשונה שאספר עליה היא שטסתי במשלחת גדו...    0
19               19  זה היה יום רגיל כמו בכל יום בשבוע קמתי ב גמור ...    0
20               20  ביום הולדתו של בן זוגי לקחתי אותו לחגוג סופש ב...    0
21               21  ביום שני כלשהו לפני מספר שבועות לאחר הסגר האחר...    0
22               22  בשנה האחרונה למדתי להכיר את עצמי יותר וללמוד ל...    0
23               23  במהלך התקופה האחרונה אני ושאר חבריי ללימודים נ...    0
24               24  הכל התחיל ביום חמישי כשיצאנו אני והצוות שלי מה...    0
25               25  השבוע נישאתי לבחירת ליבי זה היה היום המרגש ביו...    0
26               26  היי טובזאת הייתה שנה מוזרה ועמוסה בשנה הזו למד...    0
27               27  כשהייתי בן  נולד לי אח קטן אני חייב להודות שאנ...    0
28               28  כל חיי היה לי פחד גבהים החשש של להיות בגובה ול...    0
29               29  כמעט קרוב לחצי שנה שאני מתאמן לאימוני התוכנית ...    0
30               30  היום בו אבא שלי עבר אירוע מוחי לפני כחצי שנה א...    0
31               31  נסעתי עם חברים לים היה יום חם ורצינו ללכת לנצל...    0
32               32  במרץ  פרצה במדינת ישראל מגיפת הקורונה אשר המקו...    1
33               33  בתחילת שנת  אבא שלי קיבל הצעה לעשות רילוקיישן ...    0
34               34  התארסתי לחברה שלי איתה אני חוגג כבר כמעט שמנה ...    0
35               35  בחופשת קיץ בין שנה ב לשנה ג בחודש אוקטובר טסתי...    1
36               36  כאשר הייתי בן  אובחנתי עם בעיות קשב וריכוז ולא...    0
37               37  היום שבו אכלתי את השווארמה הכי טעימה בארץ הכל ...    0
38               38  במסגרת אחד הקורסים במכללה הייתי צריך ללמד אדם ...    0
39               39  שלום לכולם רציתי לספר על חוויה שלי מהשנה האחרו...    0

...


### Save output to csv (optional)
After you're done save your output to the 'classification_results.csv' csv file.<br/>
We assume that the dataframe with your results contain the following columns:
* column 1 (left column): 'test_example_id'  - the same id associated to each of the test stories to be predicted.
* column 2 (right column): 'predicted_category' - the predicted gender value for each of the associated story. 

Assuming your predicted values are in the `df_predicted` dataframe, you should save you're results as following:

In [53]:
# df_predicted.to_csv('classification_results.csv',index=False)